In [ ]:
#prophet

In [1]:
!pip install prophet

Defaulting to user installation because normal site-packages is not writeable


In [2]:
import pandas as pd
import os
from prophet import Prophet
import joblib
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import numpy as np
import matplotlib.pyplot as plt

# -----------------------------
# Paths
# -----------------------------
input_folder = "dataset"
output_models = "prophet_output_models"
output_csv = "prophet_output_csv"
output_graphs = "prophet_output_graphs"
output_metrics_csv = "prophet_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)

# -----------------------------
# Prepare metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Function to handle multiple date formats
# -----------------------------
def parse_dates(date_series):
    """Try multiple date formats and return parsed dates"""
    for fmt in ("%Y-%m-%d", "%d-%m-%Y", "%d/%m/%Y", "%m/%d/%Y"):
        try:
            return pd.to_datetime(date_series, format=fmt, errors="coerce")
        except:
            continue
    # fallback: let pandas auto-infer
    return pd.to_datetime(date_series, errors="coerce")

# -----------------------------
# Process each CSV
# -----------------------------
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"\n========== Processing: {file} ==========")

        # Load CSV
        df = pd.read_csv(file_path)

        # Parse dates
        df['Date'] = parse_dates(df['Date'])
        if df['Date'].isna().sum() > 0:
            print(f"⚠️ Warning: {df['Date'].isna().sum()} invalid dates found and dropped")
            df = df.dropna(subset=['Date'])

        df = df.sort_values('Date')

        # Handle missing values
        if df['Average Price'].isna().sum() > 0:
            mean_value = df['Average Price'].mean()
            df['Average Price'] = df['Average Price'].fillna(mean_value)
            print(f"Filled missing values with mean: {mean_value:.2f}")

        # Prepare data for Prophet
        prophet_df = df[['Date', 'Average Price']].rename(columns={'Date': 'ds', 'Average Price': 'y'})

        # Build and fit Prophet model
        model = Prophet(daily_seasonality=True)
        model.fit(prophet_df)

        # Predict for existing dates
        future = model.make_future_dataframe(periods=0)
        forecast = model.predict(future)
        df['Predicted'] = forecast['yhat'].values

        # Round Actual and Predicted to 2 decimals
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Save CSV with Actual vs Predicted
        output_df = df[['Date', 'Average Price', 'Predicted']].rename(columns={'Average Price': 'Actual'})
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_prophet_results.csv"))
        output_df.to_csv(updated_csv_path, index=False)

        # Calculate metrics
        y_true = df['Average Price'].values
        y_pred = df['Predicted'].values

        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred) / y_true)) * 100, 2)
        accuracy = round(100 - mape, 2)

        # Print metrics
        print(f"Metrics for {file}:")
        print(f"  MAE      : {mae}")
        print(f"  RMSE     : {rmse}")
        print(f"  R²       : {r2}")
        print(f"  MAPE     : {mape}%")
        print(f"  Accuracy : {accuracy}%")

        # Save metrics
        metrics_list.append({
            'File': file,
            'MAE': mae,
            'RMSE': rmse,
            'R2': r2,
            'MAPE(%)': mape,
            'Accuracy(%)': accuracy
        })

        # Save model
        model_file = os.path.join(output_models, file.replace(".csv", "_prophet_model.pkl"))
        joblib.dump(model, model_file)

        # Save Graph
        plt.figure(figsize=(10, 6))
        plt.plot(df['Date'], df['Average Price'], label='Actual', color='blue', linewidth=2)
        plt.plot(df['Date'], df['Predicted'], label='Predicted', color='red', linewidth=2, linestyle='--')
        plt.title(f"Actual vs Predicted - {file}", fontsize=14)
        plt.xlabel("Date", fontsize=12)
        plt.ylabel("Price", fontsize=12)
        plt.legend()
        plt.grid(True, alpha=0.3)
        plt.tight_layout()

        graph_path = os.path.join(output_graphs, file.replace(".csv", "_prophet_graph.png"))
        plt.savefig(graph_path)
        plt.close()

# Save all metrics to CSV
metrics_df = pd.DataFrame(metrics_list)
metrics_df.to_csv(output_metrics_csv, index=False)
print(f"\n✅ All districts processed! Metrics saved to {output_metrics_csv}, CSV results saved, and graphs generated.")


========== Processing: onion_Bagalkot_weekly.csv ==========


22:39:35 - cmdstanpy - INFO - Chain [1] start processing
22:39:35 - cmdstanpy - INFO - Chain [1] done processing


Metrics for onion_Bagalkot_weekly.csv:
  MAE      : 455.04
  RMSE     : 641.44
  R²       : 0.21
  MAPE     : 44.62%
  Accuracy : 55.38%


22:39:36 - cmdstanpy - INFO - Chain [1] start processing



========== Processing: onion_Bangalore_weekly.csv ==========


...

Metrics for onion_Tumkur_weekly.csv:
  MAE      : 384.45
  RMSE     : 618.66
  R²       : 0.88
  MAPE     : 15.13%
  Accuracy : 84.87%


22:39:54 - cmdstanpy - INFO - Chain [1] start processing



========== Processing: onion_Udupi_weekly.csv ==========


22:39:54 - cmdstanpy - INFO - Chain [1] done processing


Metrics for onion_Udupi_weekly.csv:
  MAE      : 693.09
  RMSE     : 1010.21
  R²       : 0.38
  MAPE     : 36.2%
  Accuracy : 63.8%

✅ All districts processed! Metrics saved to prophet_metrics.csv, CSV results saved, and graphs generated.


In [3]:
#ARIMA

In [3]:
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
from statsmodels.tsa.arima.model import ARIMA
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import joblib
import warnings
warnings.filterwarnings("ignore")

# -----------------------------
# Create output directories
# -----------------------------
input_folder = "dataset"
output_models = "arima_output_models"
output_csv = "arima_output_csv"
output_graphs = "arima_output_graphs"
output_logs = "arima_output_logs"
output_metrics = "arima_output_metrics"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)
os.makedirs(output_metrics, exist_ok=True)

# Metrics collector
all_metrics = []

# -----------------------------
# Helper function for flexible date parsing
# -----------------------------
def parse_dates(date_series):
    """Try multiple date formats until successful."""
    for fmt in ("%Y-%m-%d", "%d-%m-%Y", "%d/%m/%Y", "%Y/%m/%d"):
        try:
            return pd.to_datetime(date_series, format=fmt)
        except Exception:
            continue
    return pd.to_datetime(date_series, errors="coerce")  # fallback

# -----------------------------
# Process each CSV file
# -----------------------------
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"Processing: {file}")

        try:
            # Load CSV
            df = pd.read_csv(file_path)

            # Handle multiple date formats
            df['Date'] = parse_dates(df['Date'])
            df = df.dropna(subset=['Date'])
            df = df.sort_values('Date')
            df.set_index('Date', inplace=True)

            # Handle NaN values in Average Price
            df['Average Price'] = df['Average Price'].fillna(df['Average Price'].mean())

            # Add moving averages
            df['MA_7'] = df['Average Price'].rolling(window=7).mean()
            df['MA_30'] = df['Average Price'].rolling(window=30).mean()

            # ARIMA parameters (static, can be tuned later)
            p, d, q = 5, 1, 0
            model = ARIMA(df['Average Price'], order=(p, d, q))
            model_fit = model.fit()

            # Save ARIMA model
            model_file = os.path.join(output_models, file.replace(".csv", "_arima_model.pkl"))
            joblib.dump(model_fit, model_file)

            # Predictions
            predictions = model_fit.predict(start=0, end=len(df)-1, typ='levels')
            df['Predicted'] = predictions

            # Round Actual and Predicted to 2 decimals
            df['Average Price'] = df['Average Price'].round(2)
            df['Predicted'] = df['Predicted'].round(2)

            # Save Actual vs Predicted CSV
            comparison_df = pd.DataFrame({
                "Date": df.index,
                "Actual": df['Average Price'],
                "Predicted": df['Predicted']
            })
            comparison_csv = os.path.join(output_csv, file.replace(".csv", "_arima_actual_vs_predicted.csv"))
            comparison_df.to_csv(comparison_csv, index=False)

            # Calculate metrics
            mae = round(mean_absolute_error(df['Average Price'], df['Predicted']), 2)
            rmse = round(np.sqrt(mean_squared_error(df['Average Price'], df['Predicted'])), 2)
            r2 = round(r2_score(df['Average Price'], df['Predicted']), 2)
            mape = round(np.mean(np.abs((df['Average Price'] - df['Predicted']) / df['Average Price'])) * 100, 2)
            accuracy = round(100 - mape, 2)

            all_metrics.append({
                "District": file.replace(".csv", ""),
                "MAE": mae,
                "RMSE": rmse,
                "R2": r2,
                "MAPE(%)": mape,
                "Accuracy (%)": accuracy
            })

            # Print metrics
            print(f"Metrics for {file}:")
            print(f"  MAE      : {mae}")
            print(f"  RMSE     : {rmse}")
            print(f"  R²       : {r2}")
            print(f"  MAPE     : {mape}%")
            print(f"  Accuracy : {accuracy}%\n")

            # Save graph
            plt.figure(figsize=(12,6))
            plt.plot(df.index, df['Average Price'], label="Actual", color="blue", linewidth=2)
            plt.plot(df.index, df['Predicted'], label="Predicted (ARIMA)", color="red", linestyle="dashed", linewidth=2)
            plt.plot(df.index, df['MA_7'], label="MA 7", color="orange")
            plt.plot(df.index, df['MA_30'], label="MA 30", color="green")
            plt.xlabel("Date")
            plt.ylabel("Average Price")
            plt.title(f"Price Prediction (ARIMA) - {file}")
            plt.legend()
            plt.grid(True)
            graph_file = os.path.join(output_graphs, file.replace(".csv", "_arima_graph.png"))
            plt.savefig(graph_file)
            plt.close()

            # Save logs
            log_file = os.path.join(output_logs, file.replace(".csv", "_arima_training.txt"))
            with open(log_file, "w", encoding="utf-8") as f:
                f.write(f"ARIMA model fitted for {file}.\n")
                f.write(f"ARIMA Order: (p={p}, d={d}, q={q})\n")
                f.write(f"MAE: {mae}, RMSE: {rmse}, R²: {r2}, MAPE: {mape}%, Accuracy: {accuracy}%\n")
                f.write("Predictions, Graph, Logs saved.\n")

            print(f"Done with {file} | Model, CSV, Graph, Metrics, Log saved.\n")

        except Exception as e:
            print(f"Error processing {file}: {e}")

# -----------------------------
# Save all metrics in one CSV
# -----------------------------
if all_metrics:
    metrics_df = pd.DataFrame(all_metrics)
    metrics_csv = os.path.join(output_metrics, "arima_all_districts_metrics.csv")
    metrics_df.to_csv(metrics_csv, index=False)
    print(f"All metrics saved to {metrics_csv}")

Processing: onion_Bagalkot_weekly.csv
Metrics for onion_Bagalkot_weekly.csv:
  MAE      : 96.58
  RMSE     : 208.05
  R²       : 0.92
  MAPE     : 7.04%
  Accuracy : 92.96%

Done with onion_Bagalkot_weekly.csv | Model, CSV, Graph, Metrics, Log saved.

Processing: onion_Bangalore_weekly.csv
Metrics for onion_Bangalore_weekly.csv:
  MAE      : 98.82
  RMSE     : 202.64
  R²       : 0.95
  MAPE     : 4.85%
  Accuracy : 95.15%

Done with onion_Bangalore_weekly.csv | Model, CSV, Graph, Metrics, Log saved.

Processing: onion_Belgaum_weekly.csv
Metrics for onion_Belgaum_weekly.csv:
  MAE      : 147.09
  RMSE     : 286.34
  R²       : 0.92
  MAPE     : 8.47%
  Accuracy : 91.53%

Done with onion_Belgaum_weekly.csv | Model, CSV, Graph, Metrics, Log saved.

Processing: onion_Bellary_weekly.csv
Metrics for onion_Bellary_weekly.csv:
  MAE      : 93.77
  RMSE     : 164.36
  R²       : 0.91
  MAPE     : 7.24%
  Accuracy : 92.76%

Done with onion_Bellary_weekly.csv | Model, CSV, Graph, Metrics, Log sa

In [ ]:
#SARIMAX

In [4]:
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
from statsmodels.tsa.statespace.sarimax import SARIMAX
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import warnings
import joblib

warnings.filterwarnings("ignore")  # Ignore warnings

# -----------------------------
# Paths
# -----------------------------
input_folder = "dataset"
output_models = "sarimax_output_models"
output_csv = "sarimax_output_csv"
output_graphs = "sarimax_output_graphs"
output_metrics_csv = "sarimax_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)

# -----------------------------
# Metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Process each CSV
# -----------------------------
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"========== Processing: {file} ==========")

        # Load CSV
        df = pd.read_csv(file_path)

        # Handle multiple date formats
        try:
            df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        except Exception as e:
            print(f"Date conversion failed: {e}")
            continue

        df = df.dropna(subset=['Date'])  # Drop rows where date conversion failed
        df = df.sort_values('Date')
        df.set_index('Date', inplace=True)

        # Handle missing values
        if df['Average Price'].isna().sum() > 0:
            mean_value = df['Average Price'].mean()
            df['Average Price'].fillna(mean_value, inplace=True)
            print(f"Filled missing values with mean: {mean_value:.2f}")

        # Add moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean()
        df['MA_30'] = df['Average Price'].rolling(window=30).mean()

        # SARIMAX order (tune if needed)
        order = (1, 1, 1)
        seasonal_order = (1, 1, 1, 7)

        # Fit SARIMAX model
        model = SARIMAX(df['Average Price'],
                        order=order,
                        seasonal_order=seasonal_order,
                        enforce_stationarity=False,
                        enforce_invertibility=False)
        model_fit = model.fit(disp=False)

        # Save model
        model_file = os.path.join(output_models, file.replace(".csv", "_sarimax_model.pkl"))
        joblib.dump(model_fit, model_file)

        # Predictions
        df['Predicted'] = model_fit.predict(start=0, end=len(df)-1)

        # Round Actual and Predicted to 2 decimals
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Calculate metrics
        y_true = df['Average Price'].values
        y_pred = df['Predicted'].values
        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred) / y_true)) * 100, 2)
        accuracy = round(100 - mape, 2)

        # Display metrics
        print(f"Metrics for {file}:")
        print(f"  MAE      : {mae}")
        print(f"  RMSE     : {rmse}")
        print(f"  R²       : {r2}")
        print(f"  MAPE     : {mape}%")
        print(f"  Accuracy : {accuracy}%\n")

        # Save metrics to list
        metrics_list.append({
            'File': file,
            'MAE': mae,
            'RMSE': rmse,
            'R2': r2,
            'MAPE(%)': mape,
            'Accuracy(%)': accuracy
        })

        # Save Actual vs Predicted CSV
        actual_vs_pred = df[['Average Price', 'Predicted']].reset_index()
        actual_vs_pred.rename(columns={'Average Price': 'Actual'}, inplace=True)
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_sarimax_actual_vs_predicted.csv"))
        actual_vs_pred.to_csv(updated_csv_path, index=False)

        # Save graph
        plt.figure(figsize=(12,6))
        plt.plot(df.index, df['Average Price'], label="Actual", color="blue")
        plt.plot(df.index, df['MA_7'], label="MA 7", color="orange")
        plt.plot(df.index, df['MA_30'], label="MA 30", color="green")
        plt.plot(df.index, df['Predicted'], label="Predicted (SARIMAX)", color="red", linestyle="dashed")
        plt.xlabel("Date")
        plt.ylabel("Average Price")
        plt.title(f"Price Prediction (SARIMAX) - {file}")
        plt.legend()
        plt.grid(True)
        graph_file = os.path.join(output_graphs, file.replace(".csv", "_sarimax_graph.png"))
        plt.savefig(graph_file)
        plt.close()

# -----------------------------
# Save all metrics to CSV
# -----------------------------
metrics_df = pd.DataFrame(metrics_list)
metrics_df.to_csv(output_metrics_csv, index=False)

print(f"✅ All districts processed! Metrics saved to {output_metrics_csv}, predictions CSVs, graphs, and models generated.")

========== Processing: onion_Bagalkot_weekly.csv ==========
Metrics for onion_Bagalkot_weekly.csv:
  MAE      : 102.93
  RMSE     : 222.7
  R²       : 0.9
  MAPE     : 7.76%
  Accuracy : 92.24%

========== Processing: onion_Bangalore_weekly.csv ==========
Metrics for onion_Bangalore_weekly.csv:
  MAE      : 103.55
  RMSE     : 207.96
  R²       : 0.94
  MAPE     : 5.23%
  Accuracy : 94.77%

========== Processing: onion_Belgaum_weekly.csv ==========
Metrics for onion_Belgaum_weekly.csv:
  MAE      : 150.79
  RMSE     : 290.59
  R²       : 0.92
  MAPE     : 8.9%
  Accuracy : 91.1%

========== Processing: onion_Bellary_weekly.csv ==========
Metrics for onion_Bellary_weekly.csv:
  MAE      : 97.79
  RMSE     : 167.91
  R²       : 0.9
  MAPE     : 7.73%
  Accuracy : 92.27%

========== Processing: onion_Bidar_weekly.csv ==========
Metrics for onion_Bidar_weekly.csv:
  MAE      : 16.97
  RMSE     : 77.05
  R²       : 0.96
  MAPE     : 1.51%
  Accuracy : 98.49%

========== Processing: onion_Bi

In [ ]:
#TAT + MHA

In [5]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import tensorflow as tf
from tensorflow.keras import layers, models, optimizers

# -----------------------------
# Output directories
# -----------------------------
input_folder = "dataset"
output_models = "tat_output_models"
output_csv = "tat_output_csv"
output_graphs = "tat_output_graphs"
output_logs = "tat_output_logs"
metrics_file = "tat_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# -----------------------------
# Function to create dataset
# -----------------------------
def create_dataset(data, look_back=30):
    X, y = [], []
    for i in range(len(data) - look_back):
        X.append(data[i:i+look_back, 0])
        y.append(data[i+look_back, 0])
    return np.array(X), np.array(y)

# -----------------------------
# Define Temporal Attention Transformer Model
# -----------------------------
def build_tat_model(input_shape, d_model=64, num_heads=4, ff_dim=128, dropout_rate=0.2):
    inputs = layers.Input(shape=input_shape)  # (look_back, 1)
    
    # Multi-Head Attention
    x = layers.MultiHeadAttention(num_heads=num_heads, key_dim=d_model)(inputs, inputs)
    x = layers.Dropout(dropout_rate)(x)
    x = layers.LayerNormalization(epsilon=1e-6)(x + inputs)  # Residual connection
    
    # Feed-Forward Network
    ff = layers.Dense(ff_dim, activation='relu')(x)
    ff = layers.Dense(input_shape[1])(ff)
    x = layers.LayerNormalization(epsilon=1e-6)(x + ff)  # Residual connection
    
    # Global Pooling
    x = layers.GlobalAveragePooling1D()(x)
    
    # Output
    outputs = layers.Dense(1)(x)
    
    model = models.Model(inputs=inputs, outputs=outputs)
    model.compile(optimizer=optimizers.Adam(learning_rate=0.001),
                  loss='mse', metrics=['mae'])
    return model

# -----------------------------
# Metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Process each CSV file
# -----------------------------
look_back = 30
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"🚀 Processing: {file}")

        # Load CSV
        df = pd.read_csv(file_path)
        
        # Handle multiple date formats
        try:
            df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        except Exception as e:
            print(f"Date conversion failed: {e}")
            continue
        
        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Replace NaN in 'Average Price' with column mean
        df['Average Price'].fillna(df['Average Price'].mean(), inplace=True)

        # Add moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean()
        df['MA_30'] = df['Average Price'].rolling(window=30).mean()

        # Replace NaN in moving averages with column mean
        df['MA_7'].fillna(df['MA_7'].mean(), inplace=True)
        df['MA_30'].fillna(df['MA_30'].mean(), inplace=True)

        # Prepare data using MinMaxScaler
        values = df[['Average Price']].values.astype('float32')
        scaler = MinMaxScaler(feature_range=(0, 1))
        scaled_values = scaler.fit_transform(values)

        # Create sequences
        X, y = create_dataset(scaled_values, look_back)
        X = np.reshape(X, (X.shape[0], X.shape[1], 1))

        # Build model
        model = build_tat_model(input_shape=(look_back,1))
        model.summary()

        # Train model
        history = model.fit(X, y, epochs=100, batch_size=16, validation_split=0.2, verbose=1)

        # Save training logs
        log_file = os.path.join(output_logs, file.replace(".csv", "_tat_training.txt"))
        with open(log_file, "w") as f:
            f.write("Training Loss per Epoch:\n")
            for i, loss in enumerate(history.history['loss']):
                f.write(f"Epoch {i+1}: Loss={loss}, Val_Loss={history.history['val_loss'][i]}\n")

        # Predictions
        predictions = model.predict(X)
        predictions_rescaled = scaler.inverse_transform(predictions)
        df['Predicted'] = [np.nan]*look_back + list(predictions_rescaled.flatten())

        # Round Actual and Predicted to 2 decimals
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Compute metrics
        y_true = df['Average Price'].values[look_back:]
        y_pred = predictions_rescaled.flatten()
        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred) / y_true)) * 100, 2)
        accuracy = round(100 - mape, 2)

        metrics_list.append([file.replace(".csv",""), mae, rmse, r2, mape, accuracy])

        # Save model
        model_file = os.path.join(output_models, file.replace(".csv", "_tat_model.h5"))
        model.save(model_file)

        # Save CSV
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_tat_updated.csv"))
        df.to_csv(updated_csv_path, index=False)

        # Save graph
        plt.figure(figsize=(12,6))
        plt.plot(df['Date'], df['Average Price'], label='Ground Truth', color='blue')
        plt.plot(df['Date'], df['MA_7'], label='MA 7', color='orange')
        plt.plot(df['Date'], df['MA_30'], label='MA 30', color='green')
        plt.plot(df['Date'], df['Predicted'], label='Predicted (TAT)', color='red', linestyle='dashed')
        plt.xlabel('Date')
        plt.ylabel('Average Price')
        plt.title(f'Price Prediction (TAT) - {file}')
        plt.legend()
        plt.grid(True)
        graph_file = os.path.join(output_graphs, file.replace(".csv", "_tat_graph.png"))
        plt.savefig(graph_file)
        plt.close()

        print(f"✅ Done with {file} | MAE={mae}, RMSE={rmse}, R2={r2}, MAPE={mape}%, Accuracy={accuracy}%\n")

# Save all metrics
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print(f"📊 Metrics saved to {metrics_file}")

🚀 Processing: onion_Bagalkot_weekly.csv


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer (InputLayer)      │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ multi_head_attention          │ (None, 30, 1)             │           1,793 │ input_layer[0][0],         │
│ (MultiHeadAttention)          │                           │                 │ input_layer[0][0]          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dropout_1 (Dropout)           │ (None, 30, 1)             │               0 │ multi_head_attention[0][0] │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add (Add)                     │ (None, 30, 1)             │               0 │ dropout_1[0][0],           │
│                               │                           │                 │ input_layer[0][0]          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization           │ (None, 30, 1)             │               2 │ add[0][0]                  │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense (Dense)                 │ (None, 30, 128)           │             256 │ layer_normalization[0][0]  │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_1 (Dense)               │ (None, 30, 1)             │             129 │ dense[0][0]                │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_1 (Add)                   │ (None, 30, 1)             │               0 │ layer_normalization[0][0], │
│                               │                           │                 │ dense_1[0][0]              │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_1         │ (None, 30, 1)             │               2 │ add_1[0][0]                │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d      │ (None, 1)                 │               0 │ layer_normalization_1[0][… │
│ (GlobalAveragePooling1D)      │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_2 (Dense)               │ (None, 1)                 │               2 │ global_average_pooling1d[… │
└───────────────────────────────┴───────────────────────────┴─────────────────┴────────────────────────────┘

 Total params: 2,184 (8.53 KB)

 Trainable params: 2,184 (8.53 KB)

...

 Total params: 2,184 (8.53 KB)

 Trainable params: 2,184 (8.53 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 4s 16ms/step - loss: 0.0288 - mae: 0.1075 - val_loss: 0.0321 - val_mae: 0.1308
Epoch 2/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - loss: 0.0173 - mae: 0.0878 - val_loss: 0.0235 - val_mae: 0.1051
Epoch 3/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - loss: 0.0153 - mae: 0.0905 - val_loss: 0.0227 - val_mae: 0.1027
Epoch 4/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0158 - mae: 0.0902 - val_loss: 0.0229 - val_mae: 0.1034
Epoch 5/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - loss: 0.0191 - mae: 0.0978 - val_loss: 0.0228 - val_mae: 0.1029
Epoch 6/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - loss: 0.0171 - mae: 0.0945 - val_loss: 0.0226 - val_mae: 0.1025
Epoch 7/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - loss: 0.0135 - mae: 0.0874 - val_loss: 0.0227 - val_mae: 0.1027
Epoch 8/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - loss: 0.0186 - mae: 0.0964 - val_loss: 0.0227 - val_mae: 0.1027
Epoch 9/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - los

✅ Done with onion_Udupi_weekly.csv | MAE=920.38, RMSE=1304.3, R2=-0.02, MAPE=47.88%, Accuracy=52.12%

📊 Metrics saved to tat_metrics.csv


In [ ]:
#TAT + MQA

In [6]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import tensorflow as tf
from tensorflow.keras import layers, models, optimizers

# -----------------------------
# Output directories
# -----------------------------
input_folder = "dataset"
output_models = "tat_mqa_output_models"
output_csv = "tat_mqa_output_csv"
output_graphs = "tat_mqa_output_graphs"
output_logs = "tat_mqa_output_logs"
metrics_file = "tat_mqa_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# -----------------------------
# Function to create dataset
# -----------------------------
def create_dataset(data, look_back=30):
    X, y = [], []
    for i in range(len(data) - look_back):
        X.append(data[i:i+look_back, 0])
        y.append(data[i+look_back, 0])
    return np.array(X), np.array(y)

# -----------------------------
# Multi-Query Attention Layer
# -----------------------------
class MultiQueryAttention(layers.Layer):
    def __init__(self, num_heads, key_dim, dropout_rate=0.1, **kwargs):
        super(MultiQueryAttention, self).__init__(**kwargs)
        self.num_heads = num_heads
        self.key_dim = key_dim
        self.dropout_rate = dropout_rate
        self.q_dense = [layers.Dense(key_dim) for _ in range(num_heads)]
        self.k_dense = layers.Dense(key_dim)
        self.v_dense = layers.Dense(key_dim)
        self.dropout = layers.Dropout(dropout_rate)
        self.output_dense = layers.Dense(key_dim)

    def call(self, x):
        K = self.k_dense(x)
        V = self.v_dense(x)
        head_outputs = []

        for q_layer in self.q_dense:
            Q = q_layer(x)
            scores = tf.matmul(Q, K, transpose_b=True) / tf.math.sqrt(tf.cast(self.key_dim, tf.float32))
            attention_weights = tf.nn.softmax(scores, axis=-1)
            attention_output = tf.matmul(attention_weights, V)
            head_outputs.append(attention_output)

        concat = tf.concat(head_outputs, axis=-1)
        output = self.output_dense(concat)
        output = self.dropout(output)
        return output

    def get_config(self):
        config = super(MultiQueryAttention, self).get_config()
        config.update({
            "num_heads": self.num_heads,
            "key_dim": self.key_dim,
            "dropout_rate": self.dropout_rate
        })
        return config

# -----------------------------
# TAT-MQA Model
# -----------------------------
def build_tat_mqa_model(input_shape, d_model=64, num_heads=4, ff_dim=128, dropout_rate=0.2):
    inputs = layers.Input(shape=input_shape)
    x = MultiQueryAttention(num_heads=num_heads, key_dim=d_model, dropout_rate=dropout_rate)(inputs)
    x = layers.LayerNormalization(epsilon=1e-6)(x + inputs)

    ff = layers.Dense(ff_dim, activation='relu')(x)
    ff = layers.Dense(input_shape[1])(ff)
    x = layers.LayerNormalization(epsilon=1e-6)(x + ff)

    x = layers.GlobalAveragePooling1D()(x)
    outputs = layers.Dense(1)(x)

    model = models.Model(inputs=inputs, outputs=outputs)
    model.compile(optimizer=optimizers.Adam(learning_rate=0.001),
                  loss='mse', metrics=['mae'])
    return model

# -----------------------------
# Metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Process each CSV file
# -----------------------------
look_back = 30
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"🚀 Processing: {file}")

        # Load CSV
        df = pd.read_csv(file_path)

        # Handle multiple date formats
        try:
            df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        except Exception as e:
            print(f"Date conversion failed: {e}")
            continue

        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Handle NaNs
        df['Average Price'].fillna(df['Average Price'].mean(), inplace=True)

        # Moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean()
        df['MA_30'] = df['Average Price'].rolling(window=30).mean()
        df['MA_7'].fillna(df['MA_7'].mean(), inplace=True)
        df['MA_30'].fillna(df['MA_30'].mean(), inplace=True)

        # Prepare data
        values = df[['Average Price']].values.astype('float32')
        scaler = MinMaxScaler(feature_range=(0, 1))
        scaled_values = scaler.fit_transform(values)
        X, y = create_dataset(scaled_values, look_back)
        X = np.reshape(X, (X.shape[0], X.shape[1], 1))

        # Build model
        model = build_tat_mqa_model(input_shape=(look_back,1))
        model.summary()

        # Train model
        history = model.fit(X, y, epochs=100, batch_size=16, validation_split=0.2, verbose=1)

        # Save logs
        log_file = os.path.join(output_logs, file.replace(".csv", "_tat_mqa_training.txt"))
        with open(log_file, "w") as f:
            f.write("Training Loss per Epoch:\n")
            for i, loss in enumerate(history.history['loss']):
                f.write(f"Epoch {i+1}: Loss={loss}, Val_Loss={history.history['val_loss'][i]}\n")

        # Predictions
        predictions = model.predict(X)
        predictions_rescaled = scaler.inverse_transform(predictions)
        df['Predicted'] = [np.nan]*look_back + list(predictions_rescaled.flatten())

        # Round Actual and Predicted
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Metrics
        y_true = df['Average Price'].values[look_back:]
        y_pred = predictions_rescaled.flatten()
        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred) / y_true)) * 100, 2)
        accuracy = round(100 - mape, 2)
        metrics_list.append([file.replace(".csv",""), mae, rmse, r2, mape, accuracy])

        # Save model
        model_file = os.path.join(output_models, file.replace(".csv", "_tat_mqa_model.keras"))
        model.save(model_file)

        # Save CSV
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_tat_mqa_updated.csv"))
        df.to_csv(updated_csv_path, index=False)

        # Save graph
        plt.figure(figsize=(12,6))
        plt.plot(df['Date'], df['Average Price'], label='Ground Truth', color='blue')
        plt.plot(df['Date'], df['MA_7'], label='MA 7', color='orange')
        plt.plot(df['Date'], df['MA_30'], label='MA 30', color='green')
        plt.plot(df['Date'], df['Predicted'], label='Predicted (TAT-MQA)', color='red', linestyle='dashed')
        plt.xlabel('Date')
        plt.ylabel('Average Price')
        plt.title(f'Price Prediction (TAT-MQA) - {file}')
        plt.legend()
        plt.grid(True)
        graph_file = os.path.join(output_graphs, file.replace(".csv", "_tat_mqa_graph.png"))
        plt.savefig(graph_file)
        plt.close()

        print(f"✅ Done with {file} | MAE={mae}, RMSE={rmse}, R2={r2}, MAPE={mape}%, Accuracy={accuracy}%\n")

# Save metrics
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print(f"📊 Metrics saved to {metrics_file}")

🚀 Processing: onion_Bagalkot_weekly.csv



Model: "functional_23"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_23 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ multi_query_attention         │ (None, 30, 64)            │          17,216 │ input_layer_23[0][0]       │
│ (MultiQueryAttention)         │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_46 (Add)                  │ (None, 30, 64)            │               0 │ multi_query_attention[0][… │
│                               │                           │                 │ input_layer_23[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_46        │ (None, 30, 64)            │             128 │ add_46[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_76 (Dense)              │ (None, 30, 128)           │           8,320 │ layer_normalization_46[0]… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_77 (Dense)              │ (None, 30, 1)             │             129 │ dense_76[0][0]             │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_47 (Add)                  │ (None, 30, 64)            │               0 │ layer_normalization_46[0]… │
│                               │                           │                 │ dense_77[0][0]             │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_47        │ (None, 30, 64)            │             128 │ add_47[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_23   │ (None, 64)                │               0 │ layer_normalization_47[0]… │
│ (GlobalAveragePooling1D)      │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_78 (Dense)              │ (None, 1)                 │              65 │ global_average_pooling1d_… │
└───────────────────────────────┴───────────────────────────┴─────────────────┴────────────────────────────┘

 Total params: 25,986 (101.51 KB)

 Trainable params: 25,986 (101.51 KB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_45 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ multi_query_attention_22      │ (None, 30, 64)            │          17,216 │ input_layer_45[0][0]       │
│ (MultiQueryAttention)         │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_90 (Add)                  │ (None, 30, 64)            │               0 │ multi_query_attention_22[… │
│                               │                           │                 │ input_layer_45[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_90        │ (None, 30, 64)            │             128 │ add_90[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_296 (Dense)             │ (None, 30, 128)           │           8,320 │ layer_normalization_90[0]… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_297 (Dense)             │ (None, 30, 1)             │             129 │ dense_296[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_91 (Add)                  │ (None, 30, 64)            │               0 │ layer_normalization_90[0]… │
│                               │                           │                 │ dense_297[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_91        │ (None, 30, 64)            │             128 │ add_91[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_45   │ (None, 64)                │               0 │ layer_normalization_91[0]… │
│ (GlobalAveragePooling1D)      │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_298 (Dense)             │ (None, 1)                 │              65 │ global_average_pooling1d_… │
└───────────────────────────────┴───────────────────────────┴─────────────────┴────────────────────────────┘

 Total params: 25,986 (101.51 KB)

 Trainable params: 25,986 (101.51 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 6s 23ms/step - loss: 1.2344 - mae: 0.8098 - val_loss: 0.0152 - val_mae: 0.1040
Epoch 2/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - loss: 0.0269 - mae: 0.1246 - val_loss: 0.0160 - val_mae: 0.0916
Epoch 3/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - loss: 0.0273 - mae: 0.1248 - val_loss: 0.0163 - val_mae: 0.0915
Epoch 4/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - loss: 0.0226 - mae: 0.1092 - val_loss: 0.0168 - val_mae: 0.0920
Epoch 5/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - loss: 0.0174 - mae: 0.1038 - val_loss: 0.0154 - val_mae: 0.0915
Epoch 6/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - loss: 0.0238 - mae: 0.1136 - val_loss: 0.0151 - val_mae: 0.1001
Epoch 7/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - loss: 0.0182 - mae: 0.1016 - val_loss: 0.0155 - val_mae: 0.0913
Epoch 8/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - loss: 0.0179 - mae: 0.1006 - val_loss: 0.0149 - val_mae: 0.0957
Epoch 9/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - lo

In [ ]:
#TAT+GQA

In [7]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import tensorflow as tf
from tensorflow.keras import layers, models, optimizers

# -----------------------------
# Output directories
# -----------------------------
input_folder = "dataset"
output_models = "tat_gqa_output_models"
output_csv = "tat_gqa_output_csv"
output_graphs = "tat_gqa_output_graphs"
output_logs = "tat_gqa_output_logs"
metrics_file = "tat_gqa_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# -----------------------------
# Function to create dataset
# -----------------------------
def create_dataset(data, look_back=30):
    X, y = [], []
    for i in range(len(data) - look_back):
        X.append(data[i:i+look_back, 0])
        y.append(data[i+look_back, 0])
    return np.array(X), np.array(y)

# -----------------------------
# Grouped Query Attention Layer
# -----------------------------
class GroupedQueryAttention(layers.Layer):
    def __init__(self, num_groups=2, key_dim=64, dropout_rate=0.1, **kwargs):
        super(GroupedQueryAttention, self).__init__(**kwargs)
        self.num_groups = num_groups
        self.key_dim = key_dim
        self.dropout_rate = dropout_rate
        self.k_dense = layers.Dense(key_dim)
        self.v_dense = layers.Dense(key_dim)
        self.q_dense_groups = [layers.Dense(key_dim) for _ in range(num_groups)]
        self.dropout = layers.Dropout(dropout_rate)
        self.output_dense = layers.Dense(key_dim)

    def call(self, x):
        K = self.k_dense(x)
        V = self.v_dense(x)
        group_outputs = []
        for q_layer in self.q_dense_groups:
            Q = q_layer(x)
            scores = tf.matmul(Q, K, transpose_b=True) / tf.math.sqrt(tf.cast(self.key_dim, tf.float32))
            attention_weights = tf.nn.softmax(scores, axis=-1)
            attn_output = tf.matmul(attention_weights, V)
            group_outputs.append(attn_output)
        concat = tf.concat(group_outputs, axis=-1)
        output = self.output_dense(concat)
        output = self.dropout(output)
        return output

    def get_config(self):
        config = super(GroupedQueryAttention, self).get_config()
        config.update({
            "num_groups": self.num_groups,
            "key_dim": self.key_dim,
            "dropout_rate": self.dropout_rate
        })
        return config

# -----------------------------
# TAT-GQA Model
# -----------------------------
def build_tat_gqa_model(input_shape, d_model=64, num_groups=2, ff_dim=128, dropout_rate=0.2):
    inputs = layers.Input(shape=input_shape)
    x = GroupedQueryAttention(num_groups=num_groups, key_dim=d_model, dropout_rate=dropout_rate)(inputs)
    x = layers.LayerNormalization(epsilon=1e-6)(x + inputs)
    ff = layers.Dense(ff_dim, activation='relu')(x)
    ff = layers.Dense(input_shape[1])(ff)
    x = layers.LayerNormalization(epsilon=1e-6)(x + ff)
    x = layers.GlobalAveragePooling1D()(x)
    outputs = layers.Dense(1)(x)
    model = models.Model(inputs=inputs, outputs=outputs)
    model.compile(optimizer=optimizers.Adam(learning_rate=0.001),
                  loss='mse', metrics=['mae'])
    return model

# -----------------------------
# Metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Process each CSV file
# -----------------------------
look_back = 30
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"🚀 Processing: {file}")

        # Load CSV
        df = pd.read_csv(file_path)

        # Handle multiple date formats
        try:
            df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        except Exception as e:
            print(f"Date conversion failed: {e}")
            continue

        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Handle NaNs
        df['Average Price'].fillna(df['Average Price'].mean(), inplace=True)

        # Moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean()
        df['MA_30'] = df['Average Price'].rolling(window=30).mean()
        df['MA_7'].fillna(df['MA_7'].mean(), inplace=True)
        df['MA_30'].fillna(df['MA_30'].mean(), inplace=True)

        # Prepare data
        values = df[['Average Price']].values.astype('float32')
        scaler = MinMaxScaler(feature_range=(0, 1)) 
        scaled_values = scaler.fit_transform(values)
        X, y = create_dataset(scaled_values, look_back)
        X = np.reshape(X, (X.shape[0], X.shape[1], 1))

        # Build model
        model = build_tat_gqa_model(input_shape=(look_back,1), num_groups=2)
        model.summary()

        # Train model
        history = model.fit(X, y, epochs=100, batch_size=16, validation_split=0.2, verbose=1)

        # Save logs
        log_file = os.path.join(output_logs, file.replace(".csv", "_tat_gqa_training.txt"))
        with open(log_file, "w") as f:
            f.write("Training Loss per Epoch:\n")
            for i, loss in enumerate(history.history['loss']):
                f.write(f"Epoch {i+1}: Loss={loss}, Val_Loss={history.history['val_loss'][i]}\n")

        # Predictions
        predictions = model.predict(X)
        predictions_rescaled = scaler.inverse_transform(predictions)
        df['Predicted'] = [np.nan]*look_back + list(predictions_rescaled.flatten())

        # Round Actual and Predicted
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Metrics
        y_true = df['Average Price'].values[look_back:]
        y_pred = predictions_rescaled.flatten()
        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred) / y_true)) * 100, 2)
        accuracy = round(100 - mape, 2)
        metrics_list.append([file.replace(".csv",""), mae, rmse, r2, mape, accuracy])

        # Save model
        model_file = os.path.join(output_models, file.replace(".csv", "_tat_gqa_model.keras"))
        model.save(model_file)

        # Save CSV
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_tat_gqa_updated.csv"))
        df.to_csv(updated_csv_path, index=False)

        # Save graph
        plt.figure(figsize=(12,6))
        plt.plot(df['Date'], df['Average Price'], label='Ground Truth', color='blue')
        plt.plot(df['Date'], df['MA_7'], label='MA 7', color='orange')
        plt.plot(df['Date'], df['MA_30'], label='MA 30', color='green')
        plt.plot(df['Date'], df['Predicted'], label='Predicted (TAT-GQA)', color='red', linestyle='dashed')
        plt.xlabel('Date')
        plt.ylabel('Average Price')
        plt.title(f'Price Prediction (TAT-GQA) - {file}')
        plt.legend()
        plt.grid(True)
        graph_file = os.path.join(output_graphs, file.replace(".csv", "_tat_gqa_graph.png"))
        plt.savefig(graph_file)
        plt.close()

        print(f"✅ Done with {file} | MAE={mae}, RMSE={rmse}, R2={r2}, MAPE={mape}%, Accuracy={accuracy}%\n")

# Save metrics
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print(f"📊 Metrics saved to {metrics_file}")

🚀 Processing: onion_Bagalkot_weekly.csv


Model: "functional_46"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_46 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ grouped_query_attention       │ (None, 30, 64)            │           8,768 │ input_layer_46[0][0]       │
│ (GroupedQueryAttention)       │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_92 (Add)                  │ (None, 30, 64)            │               0 │ grouped_query_attention[0… │
│                               │                           │                 │ input_layer_46[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_92        │ (None, 30, 64)            │             128 │ add_92[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_304 (Dense)             │ (None, 30, 128)           │           8,320 │ layer_normalization_92[0]… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_305 (Dense)             │ (None, 30, 1)             │             129 │ dense_304[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_93 (Add)                  │ (None, 30, 64)            │               0 │ layer_normalization_92[0]… │
│                               │                           │                 │ dense_305[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_93        │ (None, 30, 64)            │             128 │ add_93[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_46   │ (None, 64)                │               0 │ layer_normalization_93[0]… │
│ (GlobalAveragePooling1D)      │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_306 (Dense)             │ (None, 1)                 │              65 │ global_average_pooling1d_… │
└───────────────────────────────┴───────────────────────────┴─────────────────┴────────────────────────────┘

 Total params: 17,538 (68.51 KB)

 Trainable params: 17,538 (68.51 KB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_68 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ grouped_query_attention_22    │ (None, 30, 64)            │           8,768 │ input_layer_68[0][0]       │
│ (GroupedQueryAttention)       │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_136 (Add)                 │ (None, 30, 64)            │               0 │ grouped_query_attention_2… │
│                               │                           │                 │ input_layer_68[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_136       │ (None, 30, 64)            │             128 │ add_136[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_480 (Dense)             │ (None, 30, 128)           │           8,320 │ layer_normalization_136[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_481 (Dense)             │ (None, 30, 1)             │             129 │ dense_480[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_137 (Add)                 │ (None, 30, 64)            │               0 │ layer_normalization_136[0… │
│                               │                           │                 │ dense_481[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_137       │ (None, 30, 64)            │             128 │ add_137[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_68   │ (None, 64)                │               0 │ layer_normalization_137[0… │
│ (GlobalAveragePooling1D)      │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_482 (Dense)             │ (None, 1)                 │              65 │ global_average_pooling1d_… │
└───────────────────────────────┴───────────────────────────┴─────────────────┴────────────────────────────┘

 Total params: 17,538 (68.51 KB)

 Trainable params: 17,538 (68.51 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 4s 15ms/step - loss: 1.2971 - mae: 0.7424 - val_loss: 0.0264 - val_mae: 0.1143
Epoch 2/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - loss: 0.0220 - mae: 0.1052 - val_loss: 0.0166 - val_mae: 0.0919
Epoch 3/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - loss: 0.0201 - mae: 0.1096 - val_loss: 0.0183 - val_mae: 0.1181
Epoch 4/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0223 - mae: 0.1134 - val_loss: 0.0176 - val_mae: 0.0928
Epoch 5/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - loss: 0.0198 - mae: 0.1070 - val_loss: 0.0172 - val_mae: 0.1140
Epoch 6/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - loss: 0.0183 - mae: 0.1010 - val_loss: 0.0147 - val_mae: 0.0936
Epoch 7/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0239 - mae: 0.1120 - val_loss: 0.0213 - val_mae: 0.1014
Epoch 8/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0248 - mae: 0.1174 - val_loss: 0.0150 - val_mae: 0.0917
Epoch 9/100
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss:

In [ ]:
#TAT+HA

In [8]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import joblib
import tensorflow as tf
from tensorflow.keras import layers, models, optimizers

# -----------------------------
# Output directories
# -----------------------------
input_folder = "dataset"
output_models = "tat_ha_output_models"
output_csv = "tat_ha_output_csv"
output_graphs = "tat_ha_output_graphs"
output_logs = "tat_ha_output_logs"
metrics_file = "tat_ha_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# -----------------------------
# Function to create dataset
# -----------------------------
def create_dataset(data, look_back=30):
    X, y = [], []
    for i in range(len(data) - look_back):
        X.append(data[i:i+look_back, 0])
        y.append(data[i+look_back, 0])
    return np.array(X), np.array(y)

# -----------------------------
# Local Attention Layer
# -----------------------------
class LocalAttention(layers.Layer):
    def __init__(self, key_dim=64, dropout_rate=0.1, **kwargs):
        super(LocalAttention, self).__init__(**kwargs)
        self.key_dim = key_dim
        self.dropout_rate = dropout_rate
        self.q_dense = layers.Dense(key_dim)
        self.k_dense = layers.Dense(key_dim)
        self.v_dense = layers.Dense(key_dim)
        self.dropout = layers.Dropout(dropout_rate)

    def call(self, x):
        Q = self.q_dense(x)
        K = self.k_dense(x)
        V = self.v_dense(x)
        scores = tf.matmul(Q, K, transpose_b=True) / tf.math.sqrt(tf.cast(tf.shape(K)[-1], tf.float32))
        weights = tf.nn.softmax(scores, axis=-1)
        output = tf.matmul(weights, V)
        output = self.dropout(output)
        return output

# -----------------------------
# Hierarchical Attention Model
# -----------------------------
def build_tat_ha_model(input_shape, d_model=64, ff_dim=128, dropout_rate=0.2):
    inputs = layers.Input(shape=input_shape)
    local_attn = LocalAttention(key_dim=d_model, dropout_rate=dropout_rate)(inputs)
    local_attn = layers.LayerNormalization(epsilon=1e-6)(local_attn + inputs)
    global_attn = layers.MultiHeadAttention(num_heads=4, key_dim=d_model)(local_attn, local_attn)
    global_attn = layers.Dropout(dropout_rate)(global_attn)
    global_attn = layers.LayerNormalization(epsilon=1e-6)(global_attn + local_attn)
    ff = layers.Dense(ff_dim, activation='relu')(global_attn)
    ff = layers.Dense(input_shape[1])(ff)
    x = layers.LayerNormalization(epsilon=1e-6)(ff + global_attn)
    x = layers.GlobalAveragePooling1D()(x)
    outputs = layers.Dense(1)(x)
    model = models.Model(inputs=inputs, outputs=outputs)
    model.compile(optimizer=optimizers.Adam(learning_rate=0.001),
                  loss='mse', metrics=['mae'])
    return model

# -----------------------------
# Metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Process each CSV file
# -----------------------------
look_back = 30
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"🚀 Processing: {file}")

        # Load CSV
        df = pd.read_csv(file_path)

        # Handle multiple date formats
        df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Handle missing Average Price
        df['Average Price'].fillna(df['Average Price'].mean(), inplace=True)

        # Moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean()
        df['MA_30'] = df['Average Price'].rolling(window=30).mean()
        df['MA_7'].fillna(df['MA_7'].mean(), inplace=True)
        df['MA_30'].fillna(df['MA_30'].mean(), inplace=True)

        # Prepare data
        values = df[['Average Price']].values.astype('float32')
        scaler = MinMaxScaler(feature_range=(0, 1))
        scaled_values = scaler.fit_transform(values)
        X, y = create_dataset(scaled_values, look_back)
        X = np.reshape(X, (X.shape[0], X.shape[1], 1))

        # Build model
        model = build_tat_ha_model(input_shape=(look_back,1))
        model.summary()

        # Train model
        history = model.fit(X, y, epochs=50, batch_size=16, validation_split=0.2, verbose=1)

        # Save logs
        log_file = os.path.join(output_logs, file.replace(".csv", "_tat_ha_training.txt"))
        with open(log_file, "w") as f:
            f.write("Training Loss per Epoch:\n")
            for i, loss in enumerate(history.history['loss']):
                f.write(f"Epoch {i+1}: Loss={loss}, Val_Loss={history.history['val_loss'][i]}\n")

        # Predictions
        predictions = model.predict(X)
        predictions_rescaled = scaler.inverse_transform(predictions)
        df['Predicted'] = [np.nan]*look_back + list(predictions_rescaled.flatten())

        # Round Actual & Predicted
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Metrics
        y_true = df['Average Price'].values[look_back:]
        y_pred = predictions_rescaled.flatten()
        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred)/y_true))*100, 2)
        accuracy = round(100 - mape, 2)
        metrics_list.append([file.replace(".csv",""), mae, rmse, r2, mape, accuracy])

        # Save model as .pkl
        model_file = os.path.join(output_models, file.replace(".csv", "_tat_ha_model.pkl"))
        joblib.dump(model, model_file)

        # Save CSV
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_tat_ha_updated.csv"))
        df.to_csv(updated_csv_path, index=False)

        # Save graph
        plt.figure(figsize=(12,6))
        plt.plot(df['Date'], df['Average Price'], label='Ground Truth', color='blue')
        plt.plot(df['Date'], df['MA_7'], label='MA 7', color='orange')
        plt.plot(df['Date'], df['MA_30'], label='MA 30', color='green')
        plt.plot(df['Date'], df['Predicted'], label='Predicted (TAT-HA)', color='red', linestyle='dashed')
        plt.xlabel('Date')
        plt.ylabel('Average Price')
        plt.title(f'Price Prediction (TAT-HA) - {file}')
        plt.legend()
        plt.grid(True)
        graph_file = os.path.join(output_graphs, file.replace(".csv", "_tat_ha_graph.png"))
        plt.savefig(graph_file)
        plt.close()

        print(f"✅ Done with {file} | MAE={mae}, RMSE={rmse}, R2={r2}, MAPE={mape}%, Accuracy={accuracy}%\n")

# Save metrics
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print(f"📊 Metrics saved to {metrics_file}")

🚀 Processing: onion_Bagalkot_weekly.csv


Model: "functional_69"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_69 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ local_attention               │ (None, 30, 64)            │             384 │ input_layer_69[0][0]       │
│ (LocalAttention)              │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_138 (Add)                 │ (None, 30, 64)            │               0 │ local_attention[0][0],     │
│                               │                           │                 │ input_layer_69[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_138       │ (None, 30, 64)            │             128 │ add_138[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ multi_head_attention_23       │ (None, 30, 64)            │          66,368 │ layer_normalization_138[0… │
│ (MultiHeadAttention)          │                           │                 │ layer_normalization_138[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dropout_94 (Dropout)          │ (None, 30, 64)            │               0 │ multi_head_attention_23[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_139 (Add)                 │ (None, 30, 64)            │               0 │ dropout_94[0][0],          │
│                               │                           │                 │ layer_normalization_138[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_139       │ (None, 30, 64)            │             128 │ add_139[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_486 (Dense)             │ (None, 30, 128)           │           8,320 │ layer_normalization_139[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_487 (Dense)             │ (None, 30, 1)             │             129 │ dense_486[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_140 (Add)                 │ (None, 30, 64)            │               0 │ dense_487[0][0],           │
│                               │                           │                 │ layer_normalization_139[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_140       │ (None, 30, 64)            │             128 │ add_140[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_69   │ (None, 64)                │               0 │ layer_normalization_140[0… │
│ (GlobalAveragePooling1D)      │                           │               

 Total params: 75,650 (295.51 KB)

 Trainable params: 75,650 (295.51 KB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_91 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ local_attention_22            │ (None, 30, 64)            │             384 │ input_layer_91[0][0]       │
│ (LocalAttention)              │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_204 (Add)                 │ (None, 30, 64)            │               0 │ local_attention_22[0][0],  │
│                               │                           │                 │ input_layer_91[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_204       │ (None, 30, 64)            │             128 │ add_204[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ multi_head_attention_45       │ (None, 30, 64)            │          66,368 │ layer_normalization_204[0… │
│ (MultiHeadAttention)          │                           │                 │ layer_normalization_204[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dropout_160 (Dropout)         │ (None, 30, 64)            │               0 │ multi_head_attention_45[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_205 (Add)                 │ (None, 30, 64)            │               0 │ dropout_160[0][0],         │
│                               │                           │                 │ layer_normalization_204[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_205       │ (None, 30, 64)            │             128 │ add_205[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_618 (Dense)             │ (None, 30, 128)           │           8,320 │ layer_normalization_205[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_619 (Dense)             │ (None, 30, 1)             │             129 │ dense_618[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_206 (Add)                 │ (None, 30, 64)            │               0 │ dense_619[0][0],           │
│                               │                           │                 │ layer_normalization_205[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_206       │ (None, 30, 64)            │             128 │ add_206[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_91   │ (None, 64)                │               0 │ layer_normalization_206[0… │
│ (GlobalAveragePooling1D)      │                           │               

 Total params: 75,650 (295.51 KB)

 Trainable params: 75,650 (295.51 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/50
38/38 ━━━━━━━━━━━━━━━━━━━━ 6s 23ms/step - loss: 0.5404 - mae: 0.5376 - val_loss: 0.0180 - val_mae: 0.1165
Epoch 2/50
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - loss: 0.0204 - mae: 0.1110 - val_loss: 0.0152 - val_mae: 0.1006
Epoch 3/50
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - loss: 0.0199 - mae: 0.1034 - val_loss: 0.0156 - val_mae: 0.0932
Epoch 4/50
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - loss: 0.0183 - mae: 0.0964 - val_loss: 0.0218 - val_mae: 0.1027
Epoch 5/50
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - loss: 0.0207 - mae: 0.0995 - val_loss: 0.0195 - val_mae: 0.1232
Epoch 6/50
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0242 - mae: 0.1145 - val_loss: 0.0152 - val_mae: 0.1005
Epoch 7/50
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0248 - mae: 0.1163 - val_loss: 0.0150 - val_mae: 0.0959
Epoch 8/50
38/38 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0157 - mae: 0.0922 - val_loss: 0.0151 - val_mae: 0.0949
Epoch 9/50
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - loss: 0.016

In [ ]:
#LSTM

In [9]:
import os
import pandas as pd
import numpy as np
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import matplotlib.pyplot as plt
import joblib
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense

# Paths
input_folder = "dataset"
output_models = "output_lstm_models"
output_csv = "output_lstm_csv"
output_graphs = "output_lstm_graphs"
output_logs = "output_lstm_logs"
metrics_file = os.path.join(output_csv, "lstm_metrics.csv")

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# Function to create sequences for LSTM
def create_sequences(data, seq_length=5):
    X, y = [], []
    for i in range(len(data) - seq_length):
        X.append(data[i:i+seq_length])
        y.append(data[i+seq_length])
    return np.array(X), np.array(y)

# Metrics storage
metrics_list = []

# Process each CSV file
seq_length = 5
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        district_name = file.split(".")[0]
        print(f"\n========== Processing: {file} ==========")
        
        # Load CSV with multiple date formats support
        df = pd.read_csv(os.path.join(input_folder, file))
        df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Fill missing Average Price
        df['Average Price'] = df['Average Price'].fillna(df['Average Price'].mean())

        # Moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean().fillna(df['Average Price'].mean())
        df['MA_30'] = df['Average Price'].rolling(window=30).mean().fillna(df['Average Price'].mean())

        # Scaling
        scaler = MinMaxScaler()
        prices_scaled = scaler.fit_transform(df['Average Price'].values.reshape(-1, 1))

        # Prepare sequences
        X, y = create_sequences(prices_scaled, seq_length)

        # Train-test split (80%-20%)
        split = int(0.8 * len(X))
        X_train, X_test = X[:split], X[split:]
        y_train, y_test = y[:split], y[split:]

        # Build LSTM model
        model = Sequential()
        model.add(LSTM(50, activation='relu', input_shape=(seq_length, 1)))
        model.add(Dense(1))
        model.compile(optimizer='adam', loss='mse', metrics=['mae'])

        # Train model
        history = model.fit(X_train, y_train, epochs=20, batch_size=32, validation_data=(X_test, y_test), verbose=1)

        # Predictions
        y_pred_scaled = model.predict(X_test)
        y_pred = scaler.inverse_transform(y_pred_scaled)
        y_true = scaler.inverse_transform(y_test.reshape(-1, 1))

        # Round Actual & Predicted
        y_true_round = np.round(y_true, 2)
        y_pred_round = np.round(y_pred, 2)

        # Save predictions in CSV
        df_pred = df.iloc[seq_length + split:].copy()
        df_pred['Predicted'] = y_pred_round.flatten()
        df_pred['Average Price'] = y_true_round.flatten()
        df_pred.to_csv(os.path.join(output_csv, f"{district_name}_lstm_updated.csv"), index=False)

        # Metrics calculation
        mae_val = round(mean_absolute_error(y_true, y_pred), 2)
        rmse_val = round(mean_squared_error(y_true, y_pred, squared=False), 2)
        r2_val = round(r2_score(y_true, y_pred), 2)
        mape_val = round(np.mean(np.abs((y_true - y_pred)/y_true))*100, 2)
        accuracy_val = round(100 - mape_val, 2)
        metrics_list.append([district_name, mae_val, rmse_val, r2_val, mape_val, accuracy_val])
        print(f"✅ Done with {file} | MAE={mae_val}, RMSE={rmse_val}, R2={r2_val}, MAPE={mape_val}%, Accuracy={accuracy_val}%")

        # Save model as .pkl
        model_file = os.path.join(output_models, f"{district_name}_lstm_model.pkl")
        joblib.dump(model, model_file)

        # Save prediction graph
        plt.figure(figsize=(12,6))
        plt.plot(df_pred['Date'], df_pred['Average Price'], label='Actual', color='blue')
        plt.plot(df_pred['Date'], df_pred['MA_7'], label='MA 7', color='orange')
        plt.plot(df_pred['Date'], df_pred['MA_30'], label='MA 30', color='green')
        plt.plot(df_pred['Date'], df_pred['Predicted'], label='Predicted', color='red', linestyle='dashed')
        plt.xlabel('Date')
        plt.ylabel('Average Price')
        plt.title(f"LSTM Predictions for {district_name}")
        plt.legend()
        plt.grid(True)
        plt.savefig(os.path.join(output_graphs, f"{district_name}_lstm_graph.png"))
        plt.close()

        # Save training loss graph
        plt.figure(figsize=(8,4))
        plt.plot(history.history['loss'], label='Train Loss')
        plt.plot(history.history['val_loss'], label='Val Loss')
        plt.title(f"Training Loss for {district_name}")
        plt.xlabel("Epochs")
        plt.ylabel("Loss")
        plt.legend()
        plt.savefig(os.path.join(output_graphs, f"{district_name}_lstm_training_loss.png"))
        plt.close()

# Save metrics CSV
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print(f"\n📊 Metrics saved to {metrics_file}")
print("\nAll districts processed successfully!")


========== Processing: onion_Bagalkot_weekly.csv ==========
Epoch 1/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 2s 26ms/step - loss: 0.0216 - mae: 0.1005 - val_loss: 0.0101 - val_mae: 0.0590
Epoch 2/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0082 - mae: 0.0593 - val_loss: 0.0049 - val_mae: 0.0482
Epoch 3/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - loss: 0.0066 - mae: 0.0534 - val_loss: 0.0035 - val_mae: 0.0350
Epoch 4/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0048 - mae: 0.0413 - val_loss: 0.0024 - val_mae: 0.0281
Epoch 5/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0047 - mae: 0.0351 - val_loss: 0.0019 - val_mae: 0.0263
Epoch 6/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0041 - mae: 0.0343 - val_loss: 0.0020 - val_mae: 0.0267
Epoch 7/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0029 - mae: 0.0305 - val_loss: 0.0018 - val_mae: 0.0256
Epoch 8/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - loss: 0.0029 - mae: 0.0309 - val_loss: 0.0017 - val_mae: 0.0261
Epoch

1/5 ━━━━━━━━━━━━━━━━━━━━ 0s 167ms/stepWARNING:tensorflow:5 out of the last 11 calls to <function TensorFlowTrainer.make_predict_function.<locals>.one_step_on_data_distributed at 0x0000022196542B60> triggered tf.function retracing. Tracing is expensive and the excessive number of tracings could be due to (1) creating @tf.function repeatedly in a loop, (2) passing tensors with different shapes, (3) passing Python objects instead of tensors. For (1), please define your @tf.function outside of the loop. For (2), @tf.function has reduce_retracing=True option that can avoid unnecessary retracing. For (3), please refer to https://www.tensorflow.org/guide/function#controlling_retracing and https://www.tensorflow.org/api_docs/python/tf/function for  more details.


5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
✅ Done with onion_Bangalore_weekly.csv | MAE=194.02, RMSE=286.65, R2=0.93, MAPE=8.79%, Accuracy=91.21%

========== Processing: onion_Belgaum_weekly.csv ==========
Epoch 1/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 3s 33ms/step - loss: 0.0174 - mae: 0.0771 - val_loss: 0.0079 - val_mae: 0.0600
Epoch 2/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0096 - mae: 0.0576 - val_loss: 0.0046 - val_mae: 0.0433
Epoch 3/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0069 - mae: 0.0497 - val_loss: 0.0037 - val_mae: 0.0384
Epoch 4/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0057 - mae: 0.0395 - val_loss: 0.0026 - val_mae: 0.0329
Epoch 5/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0037 - mae: 0.0349 - val_loss: 0.0027 - val_mae: 0.0370
Epoch 6/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - loss: 0.0024 - mae: 0.0267 - val_loss: 0.0019 - val_mae: 0.0296
Epoch 7/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0016 - mae: 0.0235 - val_loss: 0.0018

In [ ]:
#GRU

In [10]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import joblib
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import GRU, Dense, Dropout

# Paths
input_folder = "dataset"
output_models = "gru_output_models"
output_csv = "gru_output_csv"
output_graphs = "gru_output_graphs"
output_logs = "gru_output_logs"
metrics_file = os.path.join(output_csv, "gru_metrics.csv")

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# Function to create dataset sequences
def create_dataset(data, look_back=30):
    X, y = [], []
    for i in range(len(data) - look_back):
        X.append(data[i:i+look_back, 0])
        y.append(data[i+look_back, 0])
    return np.array(X), np.array(y)

# Store metrics for all files
metrics_list = []

# Process each CSV file
look_back = 30
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        district_name = file.split(".")[0]
        print(f"\n========== Processing: {file} ==========")
        
        # Load CSV with multiple date formats support
        df = pd.read_csv(os.path.join(input_folder, file))
        df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Fill missing Average Price
        df['Average Price'] = df['Average Price'].fillna(df['Average Price'].mean())

        # Moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean().fillna(df['Average Price'].mean())
        df['MA_30'] = df['Average Price'].rolling(window=30).mean().fillna(df['Average Price'].mean())

        # Prepare data
        values = df[['Average Price']].values
        scaler = MinMaxScaler(feature_range=(0, 1))
        scaled_values = scaler.fit_transform(values)

        X, y = create_dataset(scaled_values, look_back)
        X = X.reshape((X.shape[0], X.shape[1], 1))

        # Train-test split (80%-20%)
        split = int(0.8 * len(X))
        X_train, X_test = X[:split], X[split:]
        y_train, y_test = y[:split], y[split:]

        # Build GRU model
        model = Sequential()
        model.add(GRU(64, return_sequences=True, input_shape=(look_back, 1)))
        model.add(Dropout(0.2))
        model.add(GRU(32))
        model.add(Dropout(0.2))
        model.add(Dense(1))
        model.compile(optimizer="adam", loss="mse", metrics=['mae'])

        # Train model
        history = model.fit(X_train, y_train, epochs=20, batch_size=16,
                            validation_data=(X_test, y_test), verbose=1)

        # Save training log
        log_file = os.path.join(output_logs, f"{district_name}_gru_training.txt")
        with open(log_file, "w") as f:
            f.write("Epoch\tTrain_Loss\tVal_Loss\n")
            for i, (loss, val_loss) in enumerate(zip(history.history['loss'], history.history['val_loss'])):
                f.write(f"{i+1}\t{loss:.6f}\t{val_loss:.6f}\n")

        # Predict
        y_pred_scaled = model.predict(X_test)
        y_pred = scaler.inverse_transform(y_pred_scaled)
        y_true = scaler.inverse_transform(y_test.reshape(-1, 1))

        # Round Actual & Predicted
        y_true_round = np.round(y_true, 2)
        y_pred_round = np.round(y_pred, 2)

        # Save predictions in CSV
        df_pred = df.iloc[-len(y_true):].copy()
        df_pred['Predicted'] = y_pred_round.flatten()
        df_pred['Average Price'] = y_true_round.flatten()
        df_pred.to_csv(os.path.join(output_csv, f"{district_name}_gru_updated.csv"), index=False)

        # Metrics calculation
        mae_val = round(mean_absolute_error(y_true, y_pred), 2)
        rmse_val = round(mean_squared_error(y_true, y_pred, squared=False), 2)
        r2_val = round(r2_score(y_true, y_pred), 2)
        mape_val = round(np.mean(np.abs((y_true - y_pred)/y_true))*100, 2)
        accuracy_val = round(100 - mape_val, 2)
        metrics_list.append([district_name, mae_val, rmse_val, r2_val, mape_val, accuracy_val])
        print(f"✅ Done with {file} | MAE={mae_val}, RMSE={rmse_val}, R2={r2_val}, MAPE={mape_val}%, Accuracy={accuracy_val}%")

        # Save model as .pkl
        model_file = os.path.join(output_models, f"{district_name}_gru_model.pkl")
        joblib.dump(model, model_file)

        # Save prediction graph
        plt.figure(figsize=(12,6))
        plt.plot(df_pred['Date'], df_pred['Average Price'], label="Actual", color="blue")
        plt.plot(df_pred['Date'], df_pred['MA_7'], label="MA_7", color="orange")
        plt.plot(df_pred['Date'], df_pred['MA_30'], label="MA_30", color="green")
        plt.plot(df_pred['Date'], df_pred['Predicted'], label="Predicted (GRU)", color="red", linestyle="dashed")
        plt.xlabel("Date")
        plt.ylabel("Average Price")
        plt.title(f"GRU Predictions - {district_name}")
        plt.legend()
        plt.grid(True)
        plt.savefig(os.path.join(output_graphs, f"{district_name}_gru_graph.png"))
        plt.close()

        # Save training loss graph
        plt.figure(figsize=(8,4))
        plt.plot(history.history['loss'], label='Train Loss')
        plt.plot(history.history['val_loss'], label='Val Loss')
        plt.title(f"GRU Training Loss - {district_name}")
        plt.xlabel("Epochs")
        plt.ylabel("Loss")
        plt.legend()
        plt.savefig(os.path.join(output_graphs, f"{district_name}_gru_loss.png"))
        plt.close()

# Save metrics CSV
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print("\n📊 Metrics saved to", metrics_file)
print("\n✅ All districts processed successfully!")


========== Processing: onion_Bagalkot_weekly.csv ==========
Epoch 1/20
38/38 ━━━━━━━━━━━━━━━━━━━━ 6s 39ms/step - loss: 0.0104 - mae: 0.0699 - val_loss: 0.0027 - val_mae: 0.0337
Epoch 2/20
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - loss: 0.0033 - mae: 0.0359 - val_loss: 0.0018 - val_mae: 0.0297
Epoch 3/20
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - loss: 0.0033 - mae: 0.0333 - val_loss: 0.0016 - val_mae: 0.0281
Epoch 4/20
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - loss: 0.0027 - mae: 0.0322 - val_loss: 0.0014 - val_mae: 0.0251
Epoch 5/20
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - loss: 0.0021 - mae: 0.0303 - val_loss: 0.0018 - val_mae: 0.0336
Epoch 6/20
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - loss: 0.0023 - mae: 0.0316 - val_loss: 0.0014 - val_mae: 0.0216
Epoch 7/20
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - loss: 0.0025 - mae: 0.0269 - val_loss: 0.0016 - val_mae: 0.0254
Epoch 8/20
38/38 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - loss: 0.0015 - mae: 0.0238 - val_loss: 0.0011 - val_mae: 0.0212
Epo